In [17]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch import Tensor
import torch.nn.functional as F
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter

In [18]:
# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda', index=0)

In [19]:
# Convolutional neural network (two convolutional layers)
class BiGRU_AT(nn.Module):
    def __init__(self, num_classes=4):
        super(BiGRU_AT, self).__init__()
           
        self.d1 = nn.Dropout(p=0.25)      
        self.bn1 = nn.BatchNorm1d(64)
        self.gru = nn.GRU(64,256,dropout=0.25,bidirectional=True)
        self.fc1 = nn.Linear(512, 64)
        self.fc2 = nn.Linear(64, num_classes)
        #attention parameter
        self.u = torch.randn(8,device=device,requires_grad=True)
        self.fc_attention = nn.Linear(512, 8)
        self.ac_attention = nn.Softmax(dim=1)
        
    def forward(self, x):    
       
        #b,64,64
        x, _= self.gru(x)
        #b,64,256
        temp1 = self.fc_attention(x)
        temp1 = F.tanh(temp1)
        #b,64,8
        alpha = torch.tensordot(temp1,self.u,1)
        alpha = self.ac_attention(alpha)
        #b,64 = b,64,8 8
        alpha = alpha.reshape(-1,64,1)
        #b,64,1
        x = torch.mul(x,alpha)
        #b,64,256 * b,64,1 = b,64,256
        x = torch.sum(x,dim=1)
        #b,64,256 -> b,,256
        x = self.fc1(x)
        x = self.bn1(x)
        x = F.softplus(x)
        x = self.d1(x)
        x = self.fc2(x)

        return x

In [20]:
test = BiGRU_AT(4).to(device)
a = torch.randn(10,64,64)
a = a.to(device)
out = test(a)
out.shape

torch.Size([10, 4])

In [21]:
writer = SummaryWriter()

In [22]:
train_set = pd.read_csv("data/final_format/train_set.csv",header=None).to_numpy()
train_label = pd.read_csv("data/final_format/train_label.csv",header=None).to_numpy()
test_set = pd.read_csv("data/final_format/test_set.csv",header=None).to_numpy()
test_label = pd.read_csv("data/final_format/test_label.csv",header=None).to_numpy()

In [23]:
#delet first row data
train_set = train_set[1:]
train_label = train_label[1:]
test_set = test_set[1:]
test_label = test_label[1:]
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392, 1) (3598, 4096) (3598, 1)


In [24]:
train_label = train_label.reshape(-1)
test_label = test_label.reshape(-1)
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392,) (3598, 4096) (3598,)


In [25]:
#transpose to set data in time sequence
train_set = train_set.reshape(-1,64,64)
train_set = np.transpose(train_set,[0,2,1])
test_set = test_set.reshape(-1,64,64)
test_set = np.transpose(test_set,[0,2,1])
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 64, 64) (14392,) (3598, 64, 64) (3598,)


In [26]:
# Hyper parameters
num_epochs = 300
num_classes = 4
batch_size = 64
learning_rate = 1e-3

In [27]:
train_set_tensor = Tensor(train_set) 
train_label_tensor = Tensor(train_label).type(torch.LongTensor)

train_dataset = TensorDataset(train_set_tensor,train_label_tensor) 
train_loader = DataLoader(train_dataset, batch_size=batch_size) 

test_set_tensor = Tensor(test_set) 
test_label_tensor = Tensor(test_label).type(torch.LongTensor)

test_dataset = TensorDataset(test_set_tensor,test_label_tensor) 
test_loader = DataLoader(test_dataset, batch_size=batch_size) 

In [28]:
model = BiGRU_AT(num_classes).to(device)

In [29]:
# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate, weight_decay=1e-3) 
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate) 
milestones = [50,100,150,200,250]
milestones = [a * len(train_loader) for a in milestones]
scheduler = MultiStepLR(optimizer, milestones=milestones, gamma=0.5)

In [30]:
# Train the model
total_step = len(train_loader)
for epoch in range(num_epochs):
    correct=0
    total=0
    running_loss = 0
    for i, (X, Y) in enumerate(train_loader):
        X = X.to(device)
        Y = Y.to(device)
        
        
        # Forward pass
        outputs = model(X)
        loss = criterion(outputs, Y)
        
        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        #scheduler.step() 
        #print(scheduler.get_last_lr()[0])
      
        optimizer.step()
        scheduler.step() 
        #print(optimizer.param_groups[0]["lr"])
        
        _, predicted = outputs.max(1)
        total += Y.size(0)
        correct += predicted.eq(Y).sum().item()
        running_loss += loss.item()
        accu=100.*correct/total
        train_loss = running_loss/(i+1)
        print ('Epoch [{}/{}], Step [{}/{}], Training Accuracy: {:.4f}%, Training Loss: {:.4f}%'.format(epoch+1, num_epochs, i+1, total_step, accu, train_loss))
    
   
        #writer.add_scalar(f'train/accuracy', accu, epoch)
        #writer.add_scalar(f'train/loss', train_loss, epoch)
        writer.add_scalars(f'train/accuracy_loss', {
            'accuracy': accu,
            'loss': train_loss,
        }, epoch)
        

Epoch [1/300], Step [1/225], Training Accuracy: 34.3750%, Training Loss: 1.6111%
Epoch [1/300], Step [2/225], Training Accuracy: 25.0000%, Training Loss: 1.6355%
Epoch [1/300], Step [3/225], Training Accuracy: 22.9167%, Training Loss: 1.6483%
Epoch [1/300], Step [4/225], Training Accuracy: 23.4375%, Training Loss: 1.6477%
Epoch [1/300], Step [5/225], Training Accuracy: 26.2500%, Training Loss: 1.6140%
Epoch [1/300], Step [6/225], Training Accuracy: 25.5208%, Training Loss: 1.6264%
Epoch [1/300], Step [7/225], Training Accuracy: 25.4464%, Training Loss: 1.6162%
Epoch [1/300], Step [8/225], Training Accuracy: 25.5859%, Training Loss: 1.6009%
Epoch [1/300], Step [9/225], Training Accuracy: 25.3472%, Training Loss: 1.5974%
Epoch [1/300], Step [10/225], Training Accuracy: 25.3125%, Training Loss: 1.5885%
Epoch [1/300], Step [11/225], Training Accuracy: 25.4261%, Training Loss: 1.5776%
Epoch [1/300], Step [12/225], Training Accuracy: 26.0417%, Training Loss: 1.5619%
Epoch [1/300], Step [13/2

Epoch [1/300], Step [116/225], Training Accuracy: 30.1051%, Training Loss: 1.4030%
Epoch [1/300], Step [117/225], Training Accuracy: 30.1416%, Training Loss: 1.4029%
Epoch [1/300], Step [118/225], Training Accuracy: 30.1642%, Training Loss: 1.4027%
Epoch [1/300], Step [119/225], Training Accuracy: 30.1471%, Training Loss: 1.4024%
Epoch [1/300], Step [120/225], Training Accuracy: 30.1172%, Training Loss: 1.4020%
Epoch [1/300], Step [121/225], Training Accuracy: 30.1524%, Training Loss: 1.4016%
Epoch [1/300], Step [122/225], Training Accuracy: 30.2382%, Training Loss: 1.4010%
Epoch [1/300], Step [123/225], Training Accuracy: 30.2464%, Training Loss: 1.4008%
Epoch [1/300], Step [124/225], Training Accuracy: 30.2041%, Training Loss: 1.4007%
Epoch [1/300], Step [125/225], Training Accuracy: 30.1125%, Training Loss: 1.4010%
Epoch [1/300], Step [126/225], Training Accuracy: 30.0719%, Training Loss: 1.4007%
Epoch [1/300], Step [127/225], Training Accuracy: 30.0320%, Training Loss: 1.4008%
Epoc

Epoch [1/300], Step [225/225], Training Accuracy: 31.7260%, Training Loss: 1.3670%
Epoch [2/300], Step [1/225], Training Accuracy: 34.3750%, Training Loss: 1.2712%
Epoch [2/300], Step [2/225], Training Accuracy: 34.3750%, Training Loss: 1.3019%
Epoch [2/300], Step [3/225], Training Accuracy: 33.8542%, Training Loss: 1.3416%
Epoch [2/300], Step [4/225], Training Accuracy: 34.7656%, Training Loss: 1.3151%
Epoch [2/300], Step [5/225], Training Accuracy: 35.6250%, Training Loss: 1.3125%
Epoch [2/300], Step [6/225], Training Accuracy: 33.8542%, Training Loss: 1.3252%
Epoch [2/300], Step [7/225], Training Accuracy: 33.7054%, Training Loss: 1.3245%
Epoch [2/300], Step [8/225], Training Accuracy: 33.9844%, Training Loss: 1.3163%
Epoch [2/300], Step [9/225], Training Accuracy: 35.4167%, Training Loss: 1.3127%
Epoch [2/300], Step [10/225], Training Accuracy: 35.1562%, Training Loss: 1.3090%
Epoch [2/300], Step [11/225], Training Accuracy: 35.2273%, Training Loss: 1.3087%
Epoch [2/300], Step [12/

Epoch [2/300], Step [107/225], Training Accuracy: 36.3610%, Training Loss: 1.2969%
Epoch [2/300], Step [108/225], Training Accuracy: 36.4005%, Training Loss: 1.2966%
Epoch [2/300], Step [109/225], Training Accuracy: 36.2959%, Training Loss: 1.2963%
Epoch [2/300], Step [110/225], Training Accuracy: 36.3494%, Training Loss: 1.2956%
Epoch [2/300], Step [111/225], Training Accuracy: 36.3598%, Training Loss: 1.2955%
Epoch [2/300], Step [112/225], Training Accuracy: 36.3560%, Training Loss: 1.2955%
Epoch [2/300], Step [113/225], Training Accuracy: 36.2694%, Training Loss: 1.2964%
Epoch [2/300], Step [114/225], Training Accuracy: 36.2527%, Training Loss: 1.2961%
Epoch [2/300], Step [115/225], Training Accuracy: 36.2636%, Training Loss: 1.2965%
Epoch [2/300], Step [116/225], Training Accuracy: 36.3281%, Training Loss: 1.2960%
Epoch [2/300], Step [117/225], Training Accuracy: 36.2313%, Training Loss: 1.2970%
Epoch [2/300], Step [118/225], Training Accuracy: 36.2156%, Training Loss: 1.2969%
Epoc

Epoch [2/300], Step [215/225], Training Accuracy: 36.9331%, Training Loss: 1.2842%
Epoch [2/300], Step [216/225], Training Accuracy: 36.9068%, Training Loss: 1.2843%
Epoch [2/300], Step [217/225], Training Accuracy: 36.9096%, Training Loss: 1.2840%
Epoch [2/300], Step [218/225], Training Accuracy: 36.8764%, Training Loss: 1.2843%
Epoch [2/300], Step [219/225], Training Accuracy: 36.9007%, Training Loss: 1.2839%
Epoch [2/300], Step [220/225], Training Accuracy: 36.9460%, Training Loss: 1.2834%
Epoch [2/300], Step [221/225], Training Accuracy: 36.9485%, Training Loss: 1.2837%
Epoch [2/300], Step [222/225], Training Accuracy: 36.9581%, Training Loss: 1.2836%
Epoch [2/300], Step [223/225], Training Accuracy: 37.0025%, Training Loss: 1.2835%
Epoch [2/300], Step [224/225], Training Accuracy: 37.0257%, Training Loss: 1.2832%
Epoch [2/300], Step [225/225], Training Accuracy: 36.9997%, Training Loss: 1.2835%
Epoch [3/300], Step [1/225], Training Accuracy: 40.6250%, Training Loss: 1.2109%
Epoch 

...

Epoch [299/300], Step [6/225], Training Accuracy: 100.0000%, Training Loss: 0.0173%
Epoch [299/300], Step [7/225], Training Accuracy: 99.3304%, Training Loss: 0.0268%
Epoch [299/300], Step [8/225], Training Accuracy: 99.4141%, Training Loss: 0.0239%
Epoch [299/300], Step [9/225], Training Accuracy: 98.9583%, Training Loss: 0.0267%
Epoch [299/300], Step [10/225], Training Accuracy: 98.9062%, Training Loss: 0.0273%
Epoch [299/300], Step [11/225], Training Accuracy: 99.0057%, Training Loss: 0.0256%
Epoch [299/300], Step [12/225], Training Accuracy: 99.0885%, Training Loss: 0.0257%
Epoch [299/300], Step [13/225], Training Accuracy: 99.1587%, Training Loss: 0.0245%
Epoch [299/300], Step [14/225], Training Accuracy: 99.2188%, Training Loss: 0.0243%
Epoch [299/300], Step [15/225], Training Accuracy: 99.2708%, Training Loss: 0.0243%
Epoch [299/300], Step [16/225], Training Accuracy: 99.3164%, Training Loss: 0.0235%
Epoch [299/300], Step [17/225], Training Accuracy: 99.3566%, Training Loss: 0.0

Epoch [299/300], Step [113/225], Training Accuracy: 99.5022%, Training Loss: 0.0212%
Epoch [299/300], Step [114/225], Training Accuracy: 99.5066%, Training Loss: 0.0212%
Epoch [299/300], Step [115/225], Training Accuracy: 99.4837%, Training Loss: 0.0213%
Epoch [299/300], Step [116/225], Training Accuracy: 99.4881%, Training Loss: 0.0213%
Epoch [299/300], Step [117/225], Training Accuracy: 99.4925%, Training Loss: 0.0212%
Epoch [299/300], Step [118/225], Training Accuracy: 99.4968%, Training Loss: 0.0211%
Epoch [299/300], Step [119/225], Training Accuracy: 99.5011%, Training Loss: 0.0212%
Epoch [299/300], Step [120/225], Training Accuracy: 99.5052%, Training Loss: 0.0212%
Epoch [299/300], Step [121/225], Training Accuracy: 99.4964%, Training Loss: 0.0212%
Epoch [299/300], Step [122/225], Training Accuracy: 99.5005%, Training Loss: 0.0213%
Epoch [299/300], Step [123/225], Training Accuracy: 99.5046%, Training Loss: 0.0212%
Epoch [299/300], Step [124/225], Training Accuracy: 99.5086%, Tra

Epoch [299/300], Step [224/225], Training Accuracy: 99.5396%, Training Loss: 0.0206%
Epoch [299/300], Step [225/225], Training Accuracy: 99.5414%, Training Loss: 0.0206%
Epoch [300/300], Step [1/225], Training Accuracy: 100.0000%, Training Loss: 0.0111%
Epoch [300/300], Step [2/225], Training Accuracy: 100.0000%, Training Loss: 0.0087%
Epoch [300/300], Step [3/225], Training Accuracy: 100.0000%, Training Loss: 0.0104%
Epoch [300/300], Step [4/225], Training Accuracy: 100.0000%, Training Loss: 0.0097%
Epoch [300/300], Step [5/225], Training Accuracy: 100.0000%, Training Loss: 0.0108%
Epoch [300/300], Step [6/225], Training Accuracy: 100.0000%, Training Loss: 0.0115%
Epoch [300/300], Step [7/225], Training Accuracy: 100.0000%, Training Loss: 0.0128%
Epoch [300/300], Step [8/225], Training Accuracy: 100.0000%, Training Loss: 0.0122%
Epoch [300/300], Step [9/225], Training Accuracy: 100.0000%, Training Loss: 0.0122%
Epoch [300/300], Step [10/225], Training Accuracy: 99.8438%, Training Loss

Epoch [300/300], Step [114/225], Training Accuracy: 99.5751%, Training Loss: 0.0205%
Epoch [300/300], Step [115/225], Training Accuracy: 99.5788%, Training Loss: 0.0204%
Epoch [300/300], Step [116/225], Training Accuracy: 99.5824%, Training Loss: 0.0203%
Epoch [300/300], Step [117/225], Training Accuracy: 99.5726%, Training Loss: 0.0204%
Epoch [300/300], Step [118/225], Training Accuracy: 99.5630%, Training Loss: 0.0204%
Epoch [300/300], Step [119/225], Training Accuracy: 99.5667%, Training Loss: 0.0204%
Epoch [300/300], Step [120/225], Training Accuracy: 99.5703%, Training Loss: 0.0203%
Epoch [300/300], Step [121/225], Training Accuracy: 99.5739%, Training Loss: 0.0202%
Epoch [300/300], Step [122/225], Training Accuracy: 99.5774%, Training Loss: 0.0202%
Epoch [300/300], Step [123/225], Training Accuracy: 99.5681%, Training Loss: 0.0206%
Epoch [300/300], Step [124/225], Training Accuracy: 99.5590%, Training Loss: 0.0206%
Epoch [300/300], Step [125/225], Training Accuracy: 99.5500%, Tra

Epoch [300/300], Step [225/225], Training Accuracy: 99.5970%, Training Loss: 0.0203%


In [31]:
from playsound import playsound
playsound(u"sound.mp3")

In [32]:
# Test the model
model.eval()  # eval mode (batchnorm uses moving mean/variance instead of mini-batch mean/variance)
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in test_loader:
        X = X.to(device)
        Y = Y.to(device)
        outputs = model(X)
        _, predicted = torch.max(outputs.data, 1)
        total += Y.size(0)
        correct += (predicted == Y).sum().item()

    print('Test Accuracy : {} %'.format(100 * correct / total))

# Save the model checkpoint
#torch.save(model.state_dict(), 'model.ckpt')

Test Accuracy : 42.384658143413006 %
